In [3]:
import pandas as pd
import numpy as np
from datetime import datetime
import os
import random
from tqdm import tqdm

In [4]:
# 교차로정보
inter_info = pd.read_csv("inter_info.csv")
inter_info['group_no'] = 3
inter_info['main_phase_no'] = 2
display(inter_info)
inter_info.to_csv('../inter_info.csv', index=0)

inter_no        inter_name  inter_lat  inter_lon  group_no  main_phase_no
0       175    한솔삼거리(한솔마을3거리)   37.36857  127.11478         3              2
1       176           느티마을4단지   37.36724  127.11480         3              2
2       177     한솔6단지(정자동사무소)   37.36619  127.11480         3              2
3       178             신기4거리   37.36346  127.11480         3              2
4       201           느티마을4거리   37.36854  127.10984         3              2
5       202        느티마을 안촌유치원   37.36855  127.11241         3              2
6       206         상록마을 321동   37.36483  127.10981         3              2
7       210  상록4거리(상록마을입구4거리)   37.36347  127.10982         3              2

In [5]:
# # 현시구성
# phase_info = pd.read_csv("phase_info.csv")
# phase_info.drop('flow_no', axis=1, inplace=True)
# # display(phase_info)
# mg = phase_info.pivot_table(index='inter_no', columns=['phase_no', 'ring_type'], values='min_green_dur').fillna(0).astype(int)
# y = phase_info.pivot_table(index='inter_no', columns=['phase_no', 'ring_type'], values='yellow_dur').fillna(0).astype(int)
# r = phase_info.pivot_table(index='inter_no', columns=['phase_no', 'ring_type'], values='red_dur').fillna(0).astype(int)
# max_phase_no = phase_info['phase_no'].max()
# new_columns = [f'{col}{phase}{ring}' for col in ['mg', 'y', 'r'] for phase in range(1, max_phase_no + 1) for ring in ['A', 'B']]
# phase_info = pd.concat([mg, y, r], axis=1)
# phase_info.columns = new_columns
# # phase_info['main_phase'] = 2
# phase_info['mg6A'] = phase_info['mg6B'] = phase_info['mg7A'] = phase_info['mg7B'] = phase_info['mg8A'] = phase_info['mg8B']= 0
# phase_info['y6A'] = phase_info['y6B'] = phase_info['y7A'] = phase_info['y7B'] = phase_info['y8A'] = phase_info['y8B']= 0
# phase_info['r6A'] = phase_info['r6B'] = phase_info['r7A'] = phase_info['r7B'] = phase_info['r8A'] = phase_info['r8B']= 0
# phase_info = phase_info[sorted(phase_info.columns)]
# phase_info.reset_index(inplace=True)
# with pd.option_context('display.max_rows', None, 'display.max_columns', None): 
#     display(phase_info)
# phase_info.to_csv('../phase_info.csv')

In [6]:
# 방위각정보
flow_angle = pd.read_csv("flow_angle.csv")
angle = flow_angle.pivot_table(index='inter_no', columns=['phase_no', 'ring_type'], values='angle_code', aggfunc='first').fillna('NaN')
new_columns = [f'angle_{ring}{phase}' for phase in range(1, 6) for ring in ['A', 'B']]
angle.columns = new_columns
angle['angle_A6'] = angle['angle_A7'] = angle['angle_A8'] = np.nan
angle['angle_B6'] = angle['angle_B7'] = angle['angle_B8'] = np.nan
angle = angle[sorted(angle.columns)]
angle = angle.reset_index()
display(angle)
angle.to_csv('../angle.csv')

inter_no angle_A1 angle_A2 angle_A3 angle_A4 angle_A5  angle_A6  angle_A7  \
0       175   179004   001095   090270   268000      NaN       NaN       NaN   
1       176   180000   180000   270356      NaN      NaN       NaN       NaN   
2       177   180000   000090     stop   268000      NaN       NaN       NaN   
3       178   180000   000090   270000   090270      NaN       NaN       NaN   
4       201   180000   270000   090270   090270   000090       NaN       NaN   
5       202   090270     stop      NaN      NaN      NaN       NaN       NaN   
6       206   180000     stop   180000     stop      NaN       NaN       NaN   
7       210   090270   268000   359090   180000      NaN       NaN       NaN   

   angle_A8 angle_B1 angle_B2 angle_B3 angle_B4 angle_B5  angle_B6  angle_B7  \
0       NaN   003176   179270   090180   270090      NaN       NaN       NaN   
1       NaN   359180   180270      NaN      NaN      NaN       NaN       NaN   
2       NaN   001176   179270      NaN   090180      NaN       NaN       NaN   
3       NaN   000180   180270   270090   090180      NaN       NaN       NaN   
4       NaN   180270   270090   270090   090180   000180       NaN       NaN   
5       NaN   270090      NaN      NaN      NaN      NaN       NaN       NaN   
6       NaN   000180      NaN   000180      NaN      NaN       NaN       NaN   
7       NaN      NaN   270090   000180   180270      NaN       NaN       NaN   

   angle_B8  
0       NaN  
1       NaN  
2       NaN  
3       NaN  
4       NaN  
5       NaN  
6       NaN  
7       NaN

In [7]:
def generate_moves():
    # 이동류번호
    plan = pd.read_csv("time_plan.csv")
    phase = pd.read_csv('phase_info.csv')
    plan = plan[plan.ID.isin([1, 5, 8, 11])]
    ID2starttime = {1:"00:00", 5:"07:00", 8:"09:00", 11:"18:30"}
    plan['start_hour'] = plan.ID.apply(lambda id:ID2starttime[id].split(":")[0])
    plan['start_minute']=plan.ID.apply(lambda id:ID2starttime[id].split(":")[1])
    plan = plan[['inter_no', 'start_hour', 'start_minute', 'phase_no', 'ring_type', 'duration', 'cycle']]
    plan_ = pd.merge(plan, phase[['inter_no', 'phase_no', 'ring_type', 'flow_no']], on=['inter_no', 'phase_no', 'ring_type'], how='left')
    plan_['flow_no'] = plan_['flow_no'].fillna(18).astype(int)
    plan_['start_second'] = plan_.start_hour.astype(int)*3600 + plan_.start_minute.astype(int)*60
    plan_ = plan_[['inter_no', 'start_second', 'phase_no', 'ring_type', 'duration', 'flow_no', 'cycle']]
    cycle_dict = dict(zip(zip(plan_['inter_no'], plan_['start_second']), plan_['cycle']))
    df = plan_[['inter_no','start_second','cycle']].drop_duplicates()
    df = df.reset_index(drop=True)
    df['start_second_exact'] = 0
    for i in range(1, len(df)):
        if i % 4 != 0:
            prev = df.loc[i-1, 'start_second_exact']
            start_second = df.loc[i, 'start_second']
            cycle = df.loc[i-1, 'cycle']
            df.loc[i, 'start_second_exact'] = (start_second - prev) % cycle + start_second
    plan_ = plan_.pivot_table(index=['inter_no', 'start_second', 'phase_no'],
                                    columns='ring_type',
                                    values=['duration', 'flow_no'],
                                    aggfunc='first').reset_index()
    plan_.columns = ['inter_no', 'start_second', 'phase_no', 'dura_A', 'dura_B', 'move_A', 'move_B']
    inter2no_phase = {inter_no:group.phase_no.unique().max() for (inter_no, group) in plan.groupby('inter_no')}

    midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
    next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
    for current_time in tqdm(range(midnight, next_day, 5)):
        sec = current_time - midnight
        the_start_second = np.max(df.start_second[df.start_second <= sec])
        move = []
        for inter_no in plan_.inter_no.unique():
            cycle = cycle_dict[(inter_no, the_start_second)]
            df = plan_[(plan_.inter_no==inter_no)&(plan_.start_second==the_start_second)].reset_index(drop=True)
            remainder = sec % cycle
            df['cums_A'] = df.copy().dura_A.cumsum()
            df['cums_B'] = df.copy().dura_B.cumsum()
            ind_A = len(df.cums_A[df.cums_A <= remainder]) % inter2no_phase[inter_no]
            ind_B = len(df.cums_B[df.cums_B <= remainder]) % inter2no_phase[inter_no]
            phas_A = df.loc[ind_A, 'phase_no']
            phas_B = df.loc[ind_B, 'phase_no']
            move_A = df.loc[ind_A, 'move_A']
            move_B = df.loc[ind_B, 'move_B']
            move.append(pd.DataFrame({'inter_no':[inter_no], 'phas_A':[phas_A], 'phas_B':[phas_B], 'move_A':[move_A], 'move_B':[move_B]}))
        move = pd.concat(move)
        move.to_csv(f'../move/move_{current_time}.csv')
    display(move)
# generate_moves()

In [8]:
# 신호계획
plan = pd.read_csv("time_plan.csv")
plan = plan[plan.ID.isin([1, 5, 8, 11])]
ID2starttime = {1:"00:00", 5:"07:00", 8:"09:00", 11:"18:30"}
plan['start_hour'] = plan.ID.apply(lambda id:ID2starttime[id].split(":")[0])
plan['start_minute']=plan.ID.apply(lambda id:ID2starttime[id].split(":")[1])
plan = plan[['inter_no', 'start_hour', 'start_minute', 'phase_no', 'ring_type', 'duration', 'cycle', 'offset']]
plan = plan.pivot_table(index=['inter_no', 'start_hour', 'start_minute', 'cycle', 'offset'], columns=['phase_no','ring_type'], values='duration', aggfunc='first').fillna(0).astype(int)
new_columns = [f'dura_{ring}{phase}' for phase in range(1, 6) for ring in ['A', 'B']]
plan.columns = new_columns
new_columns = [f'dura_{ring}{phase}' for phase in range(1, 9) for ring in ['A', 'B']]
for col in new_columns:
    if col not in plan.columns:
        plan[col] = 0
plan.reset_index(inplace=True)
plan = plan[list(plan.columns)[:3] + sorted(plan.columns)[1:-4] + list(plan.columns)[3:5]]

yellow_columns = [f'yellow_{ring}{phase}' for phase in range(1, 9) for ring in ['A', 'B']]
red_columns = [f'red_{ring}{phase}' for phase in range(1, 9) for ring in ['A', 'B']]

inter_nos = plan.inter_no.unique()
yellow_list = np.random.choice([3, 4, 5], size=plan.inter_no.nunique(), p=[0.1, 0.7, 0.2])
inter2yellow = dict(zip(inter_nos, yellow_list))
red_list = np.random.choice([0, 1, 2], size=plan.inter_no.nunique(), p=[0.1, 0.7, 0.2])
inter2red = dict(zip(inter_nos, red_list))

for phase in range(1, 9):
    for ring in ['A', 'B']:
        plan[f'yellow_{ring}{phase}'] = plan['inter_no'].map(inter2yellow)
for phase in range(1, 9):
    for ring in ['A', 'B']:
        plan[f'red_{ring}{phase}'] = plan['inter_no'].map(inter2red)

plan.to_csv('../plan.csv', index=0)
pland = plan.copy()
cums_A = np.array(pland[[f'dura_A{k}' for k in range(1,9)]].cumsum(axis=1))
cums_B = np.array(pland[[f'dura_B{k}' for k in range(1,9)]].cumsum(axis=1))
detailed_cums = []
i = 0
for row_A, row_B in zip(cums_A, cums_B):
    combined_row = np.unique(np.concatenate((row_A, row_B)))
    ddur = np.concatenate(([combined_row[0]], np.diff(combined_row)))
    ddur = np.pad(ddur, (0, 8 - len(ddur)), constant_values=(0))
    detailed_cums.append(ddur)
    for j in range(8):
        pland.at[i, f'ddur_{j+1}'] = ddur[j]
    i+=1
pland = pland[['inter_no', 'start_hour', 'start_minute'] + [f'ddur_{i}' for i in range(1,9)] + ['cycle', 'offset']] # plan detailed
pland[[f'ddur_{i}' for i in range(1,9)]] = pland[[f'ddur_{i}' for i in range(1,9)]].astype(int)
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(plan)

inter_no start_hour start_minute  dura_A1  dura_A2  dura_A3  dura_A4  \
0        175         00           00       37       39       55       29   
1        175         07           00       40       42       55       33   
2        175         09           00       43       45       55       37   
3        175         18           30       46       48       55       41   
4        176         00           00       37       73       40        0   
5        176         07           00       37       93       40        0   
6        176         09           00       37      103       40        0   
7        176         18           30       37      113       40        0   
8        177         00           00       36       20       68       26   
9        177         07           00       40       25       71       34   
10       177         09           00       43       27       70       40   
11       177         18           30       45       32       77       36   
12       178         00           00       38       39       40       23   
13       178         07           00       38       39       42       41   
14       178         09           00       38       39       43       50   
15       178         18           30       38       39       44       59   
16       201         00           00       24       24       17       58   
17       201         07           00       30       36       18       58   
18       201         09           00       33       36       25       58   
19       201         18           30       36       50       18       58   
20       202         00           00       39      101        0        0   
21       202         07           00       46      114        0        0   
22       202         09           00       46      114        0        0   
23       202         18           30       48      122        0        0   
24       206         00           00       33       35       26       26   
25       206         07           00       44       44       26       26   
26       206         09           00       45       53       26       26   
27       206         18           30       46       62       26       26   
28       210         00           00       43       29       56       22   
29       210         07           00       43       39       65       23   
30       210         09           00       43       43       70       24   
31       210         18           30       43       47       75       25   

    dura_A5  dura_A6  dura_A7  dura_A8  dura_B1  dura_B2  dura_B3  dura_B4  \
0         0        0        0        0       37       39       25       59   
1         0        0        0        0       40       42       29       59   
2         0        0        0        0       43       45       33       59   
3         0        0        0        0       46       48       37       59   
4         0        0        0        0       37       73       40        0   
5         0        0        0        0       37       93       40        0   
6         0        0        0        0       37      103       40        0   
7         0        0        0        0       37      113       40        0   
8         0        0        0        0       36       20       68       26   
9         0        0        0        0       40       25       71       34   
10        0        0        0        0       43       27       70       40   
11        0        0        0        0       45       32       77       36   
12        0        0        0        0       38       39       40       23   
13        0        0        0        0       38       39       62       21   
14        0        0        0        0       38       39       71       22   
15        0        0        0        0       38       39       80       23   
16       17        0        0        0       24       24       17       58   
17       18        0        0        0       30       36       18       58   
18       18  

In [9]:
# 신호이력
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
plan['end_unix'] = plan['start_hour'].astype(int) * 3600 + plan['start_minute'].astype(int) * 60 + midnight # 각 plan의 마지막 시점
history = []
for inter_no in plan.inter_no.unique():
    aplan = plan[plan.inter_no == inter_no] # a (specific) plan
    rows = []
    current_time = midnight # 현재시각
    for i in range(len(aplan)):
        first_row = aplan.iloc[i]
        cycle = first_row['cycle']
        unix_end = aplan.iloc[i + 1]['end_unix'] if i < len(aplan) - 1 else next_day # a plan의 마지막 시점
        r = 0
        while current_time <= unix_end:
            remainder = current_time % 10
            if remainder != 0:  # 현재시각의 일의자리가 0이 아니면 다음 현재시각의 일의자리가 0이 되도록 맞춰준다.
                r = (5 - remainder) % 10 - 5 # 1>-1, 2>-2, 3>-3, 4>-4, 5>-5, 6>4, 7>3, 8>2, 9>1
            else:
                r = random.choices([0, -1, 1], weights=[10, 1, 1])[0] # 측정오차
            # 0.001의 확률로 결측 발생
            if random.random() < 0.001: # 주기의 배수만큼 결측
                n = random.randint(0,100)
                current_time += n * cycle + r
            # 0.01의 확률로 이상치 발생
            elif random.random() > 0.99: # 카이제곱분포값 * 주기만큼의 이상치 발생. 카이제곱분포값은 항상 양수이고 평균이 1
                current_time += int(np.random.normal()**2 * cycle) + r
            else:
                current_time += cycle + r # 결측/이상 없음
            new_row = first_row.copy()
            new_row['end_unix'] = current_time
            rows.append(new_row)
    ahistory = pd.concat(rows, axis=1).transpose().reset_index(drop=True) # a (specific) history
    history.append(ahistory)
history = pd.concat(history)
history = history[history.end_unix <= next_day]
history = history.sort_values(by='end_unix').reset_index(drop=True)
history = history[['inter_no', 'end_unix'] + [f'dura_{alph}{j}' for alph in ['A', 'B'] for j in range(1,9)] + ['cycle', 'offset']]
history.to_csv('../history.csv', index=0)
history[:20]

inter_no    end_unix dura_A1 dura_A2 dura_A3 dura_A4 dura_A5 dura_A6  \
0       206  1704380520      33      35      26      26       0       0   
1       202  1704380539      39     101       0       0       0       0   
2       178  1704380540      38      39      40      23       0       0   
3       210  1704380549      43      29      56      22       0       0   
4       177  1704380550      36      20      68      26       0       0   
5       176  1704380550      37      73      40       0       0       0   
6       175  1704380559      37      39      55      29       0       0   
7       206  1704380640      33      35      26      26       0       0   
8       202  1704380680      39     101       0       0       0       0   
9       178  1704380680      38      39      40      23       0       0   
10      177  1704380700      36      20      68      26       0       0   
11      176  1704380700      37      73      40       0       0       0   
12      210  1704380700      43      29      56      22       0       0   
13      175  1704380720      37      39      55      29       0       0   
14      201  1704380736      24      24      17      58      17       0   
15      206  1704380760      33      35      26      26       0       0   
16      178  1704380819      38      39      40      23       0       0   
17      202  1704380820      39     101       0       0       0       0   
18      177  1704380849      36      20      68      26       0       0   
19      210  1704380850      43      29      56      22       0       0   

   dura_A7 dura_A8 dura_B1 dura_B2 dura_B3 dura_B4 dura_B5 dura_B6 dura_B7  \
0        0       0      33      35      26      26       0       0       0   
1        0       0      39     101       0       0       0       0       0   
2        0       0      38      39      40      23       0       0       0   
3        0       0      24      48      56      22       0       0       0   
4        0       0      36      20      68      26       0       0       0   
5        0       0      37      73      40       0       0       0       0   
6        0       0      37      39      25      59       0       0       0   
7        0       0      33      35      26      26       0       0       0   
8        0       0      39     101       0       0       0       0       0   
9        0       0      38      39      40      23       0       0       0   
10       0       0      36      20      68      26       0       0       0   
11       0       0      37      73      40       0       0       0       0   
12       0       0      24      48      56      22       0       0       0   
13       0       0      37      39      25      59       0       0       0   
14       0       0      24      24      17      58      17       0       0   
15       0       0      33      35      26      26       0       0       0   
16       0       0      38      39      40      23       0       0       0   
17       0       0      39     101       0       0       0       0       0   
18       0       0      36      20      68      26       0       0       0   
19       0       0      24      48      56      22       0       0       0   

   dura_B8 cycle offset  
0        0   120     10  
1        0   140    103  
2        0   140     50  
3        0   150    115  
4        0   150     35  
5        0   150    131  
6        0   160     57  
7        0   120     10  
8        0   140    103  
9        0   140     50  
10       0   150     35  
11       0   150    131  
12       0   150    115  
13       0   160     57  
14       0   140    133  
15       0   120     10  
16       0   140     50  
17       0   140    103  
18       0   150     35  
19       0   150    115

In [10]:
# # 신호이력
# midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
# next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
# pland['end_unix'] = pland['start_hour'].astype(int) * 3600 + pland['start_minute'].astype(int) * 60 + midnight # 각 plan의 마지막 시점
# history = []
# for inter_no in pland.inter_no.unique():
#     aplan = pland[pland.inter_no == inter_no] # a (specific) plan
#     rows = []
#     current_time = midnight # 현재시각
#     for i in range(len(aplan)):
#         first_row = aplan.iloc[i]
#         cycle = first_row['cycle']
#         unix_end = aplan.iloc[i + 1]['end_unix'] if i < len(aplan) - 1 else next_day # a plan의 마지막 시점
#         r = 0
#         while current_time <= unix_end:
#             remainder = current_time % 10
#             if remainder != 0:  # 현재시각의 일의자리가 0이 아니면 다음 현재시각의 일이자리가 0이 되도록 맞춰준다.
#                 r = (5 - remainder) % 10 - 5 # 1>-1, 2>-2, 3>-3, 4>-4, 5>-5, 6>4, 7>3, 8>2, 9>1
#             else:
#                 r = random.choices([0, -1, 1], weights=[10, 1, 1])[0] # 측정오차
#             # 0.001의 확률로 결측 발생
#             if random.random() < 0.001: # 주기의 배수만큼 결측
#                 n = random.randint(0,100)
#                 current_time += n * cycle + r
#             # 0.01의 확률로 이상치 발생
#             elif random.random() > 0.99: # 카이제곱분포값 * 주기만큼의 이상치 발생. 카이제곱분포값은 항상 양수이고 평균이 1
#                 current_time += int(np.random.normal()**2 * cycle) + r
#             else:
#                 current_time += cycle + r # 결측/이상 없음
#             new_row = first_row.copy()
#             new_row['end_unix'] = current_time
#             rows.append(new_row)
#     ahistory = pd.concat(rows, axis=1).transpose().reset_index(drop=True) # a (specific) history
#     history.append(ahistory)
# history = pd.concat(history)
# history = history[history.end_unix <= next_day]
# history = history.sort_values(by='end_unix').reset_index(drop=True)
# history = history[['inter_no', 'end_unix'] + [f'ddur_{j}' for j in range(1, 9)] + ['cycle', 'offset']]
# history.to_csv('../history.csv')
# display(history[:30])
# # hist = history.copy()[history.inter_no==175]
# # hist['diff'] = hist['end_unix'].diff()
# # with pd.option_context('display.max_rows', None, 'display.max_columns', None):
# #     display(hist)

In [24]:
uturn = pd.read_csv('U_TURN.csv')
uturn = uturn.rename(columns={'inode_id':'parent_id', 'unode_id':'child_id', 'adj_from_edge_id':'head_edge_id'})
uturn = uturn[['parent_id', 'child_id', 'head_edge_id', 'from_edge_id', 'to_edge_id']]
uturn.to_csv('../uturn.csv', index=0)

In [12]:
# 교차로-노드 매칭
inter_node = pd.read_csv('inter.csv')
inter_node = inter_node[['INT_NO', 'node_id', 'P/C']]
# inter_node.drop(index=len(inter_node) - 1, inplace=True)
inter_node.columns = ['inter_no', 'node_id', 'inter_type'] # parent : 주교차로, child : 부교차로
inter_node['inter_no'] = inter_node['inter_no'].astype(int) # i : intersection, u : u-turn intersection, c : coupling intersection
inter_node = pd.concat([inter_node, pd.DataFrame({'inter_no':[178], 'node_id':['c30'], 'inter_type':['child']})]).reset_index(drop=True)
inter_node.to_csv('../inter_node.csv', index=0)
display(inter_node)

inter_no node_id inter_type
0        175      i0     parent
1        175     u00      child
2        176      i1     parent
3        177      i2     parent
4        177     u20      child
5        178      i3     parent
6        178     u30      child
7        178     u31      child
8        178     u32      child
9        201      i8     parent
10       202      i9     parent
11       206      i7     parent
12       210      i6     parent
13       210     u60      child
14       178     c30      child

In [10]:
import sys
sys.path.append('../../../Scripts')

from preprocess_daily import DailyPreprocessor

In [11]:
self = DailyPreprocessor()

self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
self.make_match6()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:13<00:00, 1265.14it/s]


In [12]:
self.match7 = self.match6.copy()
self.match7 = self.match7[['inter_no', 'move_no', 'inc_dir', 'out_dir', 'inc_edge', 'out_edge', 'node_id']]

# parent_ids = sorted(self.inter_node[self.inter_node.inter_type=='parent'].node_id.unique())
# child_ids = sorted(self.inter_node[self.inter_node.inter_type=='child'].node_id.unique())

# (1) 가능한 (진입방향, 진출방향) 목록 
flows = self.nema.dropna().apply(lambda row: (row['inc_dir'], row['out_dir']), axis=1).tolist()
# (2) 각 교차로별 방향 목록 : pdires (possible directions)
pdires = {}
for node_id in self.parent_ids:
    dires = self.match7[self.match7.node_id == node_id][['inc_dir','out_dir']].values.flatten()
    dires = {dire for dire in dires if type(dire)==str}
    pdires[node_id] = dires
# (3) 각 (교차로, 진입방향) 별 진입id 목록 : inc2id (incoming direction to incoming edge_id)
inc2id = {}
for node_id in self.parent_ids:
    for inc_dir in pdires[node_id]:
        df = self.match7[(self.match7.node_id==node_id) & (self.match7.inc_dir==inc_dir)]
        inc2id[(node_id, inc_dir)] = df.inc_edge.iloc[0]
# (4) 각 (교차로, 진출방향) 별 진출id 목록 : out2id (outgoing direction to outgoing edge_id)
out2id = {}
for node_id in self.parent_ids:
    for out_dir in pdires[node_id]:
        df = self.match7[(self.match7.node_id==node_id) & (self.match7.out_dir==out_dir)]
        out2id[(node_id, out_dir)] = df.out_edge.iloc[0]
# (5) 각 교차로별 가능한 (진입방향, 진출방향) 목록 : pflow (possible flows)
pflow = {}
for node_id in self.parent_ids:
    pflow[node_id] = [flow for flow in flows if set(flow).issubset(pdires[node_id])]

In [13]:
inc_dir2angles = dict()
out_dir2angles = dict()
for inter_no in self.match4.inter_no.unique():
    df = self.match4[self.match4.inter_no==inter_no].dropna()
    inc_dir2angle = dict(zip(df['inc_dir'], df['inc_angle']))
    out_dir2angle = dict(zip(df['out_dir'], df['out_angle']))
    inc_dir2angles[inter_no] = inc_dir2angle
    out_dir2angles[inter_no] = out_dir2angle

In [14]:
angles = []
for inter_no in self.inter_nos:
    node_id = self.inter2node[inter_no]
    flows = pflow[node_id]
    inc_dir2angle = inc_dir2angles[inter_no]
    out_dir2angle = out_dir2angles[inter_no]
    for (inc_dire, out_dire) in flows:
        inc_angle = inc_dir2angle[inc_dire]
        out_angle = out_dir2angle[out_dire]
        angle_code = inc_angle + out_angle
        nema_row = self.nema[(self.nema.inc_dir==inc_dire)&(self.nema.out_dir==out_dire)]
        move_no = nema_row.iloc[0].move_no
        angle = pd.DataFrame({'inter_no':[inter_no],'move_no':[move_no], 'angle_code':[angle_code]})
        angles.append(angle)
angles = pd.concat(angles).reset_index(drop=True)
angles.to_csv('../angle_new.csv')